In [91]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from pandas_profiling import ProfileReport
from pandas_profiling.utils.cache import cache_file
import ppscore as pps
import lightgbm as lgb
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score

# Análisis exploratorio "Ordenes de compra PORTAL 1K"

El objetivo del análisis exploratorio de datos es resumir y visualizar las principales características del conjunto de datos para extraer, entender y establecer relación entre variables. Busca determinar las características de mayor impacto a partir de la aplicación de técnicas como:

<ol>
  <li> Estadística descriptiva</li>
  <li> Agrupamiento</li>  
  <li> Correlación</li>
  <li> Análisis de variaciones</li>
</ol>

# Acerca del DataSet

El DataSet "Ordenes de compra PORTAL 1K" corresponde a una muestra de transacciones que realizan los compradores a los proveedores en el portal para los diferentes productos y servicios. Contiene tanto variables numéricas como categóricas. La información de las variables y su contenido se presentan a continuación:

 NÚMERO PEDIDO           
 ORDEN NÚMERO           
 FECHA ORDEN            
 FECHA ENTREGA          
 FECHA APROBACIÓN       
 CATEGORÍA              
 SUBCATEGORÍA           
 PROVEEDOR              
 USUARIO                
 USUARIO APROBADOR      
 DIRECCIÓN DE  ENTREGA  
 DIRECCIÓN FACTURACIÓN  
 CENTRO COSTO           
 PRESUPUESTO            
 comPAÑÍA comPRADORA    
 ESTADO                 
 PRODUCTO O SERVICIO    
 CÓDIGO PRODUCTO        
 CANTIDAD PEDIDA        
 CANTIDAD RECIBIDA      
 PRECIO UNITARIO        
 PRECIO UNITARIO + IVA  
 IVA                    
 TOTAL SIN IVA          
 TOTAL + IVA            
 FECHA ÚLTIMO MOVIMIENTO


In [58]:
#Read Dataset
#pd.set_option("display.max_columns",40)
df = pd.read_csv(r"D:\Ordenes_de_compra_PORTAL_1K.csv", sep=',', header= 0, na_values = ["  "],encoding='latin-1')
df.head()

NÚMERO PEDIDO ORDEN NÚMERO FECHA ORDEN FECHA ENTREGA FECHA APROBACION  \
0       # 49561       # 2582  11/10/2021    11/10/2021       11/10/2021   
1       # 49560       # 2581  11/10/2021    11/11/2021       11/10/2021   
2       # 49559       # 2580  11/10/2021    11/10/2021       11/10/2021   
3       # 49558       # 1892  11/10/2021    11/12/2021       11/10/2021   
4       # 49557          # 1  11/10/2021     11/9/2021       11/10/2021   

                   CATEGORÍA  \
0  Eléctricos y Electrónicos   
1      Mercadeo y publicidad   
2        Alimentos y Bebidas   
3        Alimentos y Bebidas   
4      Imprenta y litografía   

                                       SUBCATEGORIA    PROVEEDOR  \
0  Lámparas y bombillas y componentes para lámparas  Proveedor 1   
1                                        Publicidad  Proveedor 2   
2                Alimentos preparados y conservados  Proveedor 3   
3               Productos de carne y aves de corral  Proveedor 4   
4                                              Otra  Proveedor 5   

                 USUARIO    USUARIO APROBADOR  ...  \
0  Usuario solicitante 1  Usuario Aprobador 1  ...   
1  Usuario solicitante 2  Usuario Aprobador 2  ...   
2  Usuario solicitante 3  Usuario Aprobador 3  ...   
3  Usuario solicitante 4  Usuario Aprobador 4  ...   
4  Usuario solicitante 5  Usuario Aprobador 5  ...   

                            PRODUCTO O SERVICIO CODIGO PORTAL CANTIDAD PEDIDA  \
0  PANEL LED SOBREPONER 24W REDONDO LUZ BLANCA       1.20E+12             2.0   
1                       ACTIVIDADES COMERCIALES       1K15774             1.0   
2                                       Lasagna        1K7609            10.0   
3                 Pecho de Res Limpio/Sin Grasa       1K15459            50.0   
4                 LIBRO CABEZA, CORAZON Y MANOS       1K15761             7.0   

  CANTIDAD RECIBIDA PRECIO UNITARIO PRECIO UNITARIO + IVA     IVA  \
0               NaN           23364                 27803    4439   
1               1.0         1476972               1757597  280625   
2               NaN             155                   155       0   
3               NaN              22                    22       0   
4               7.0           92084                 10958   17496   

  TOTAL SIN IVA  TOTAL + IVA  FECHA ULTIMO MOVIMIENTO  
0         46728        55606               11/10/2021  
1       1476972      1757597               11/10/2021  
2           155          155               11/10/2021  
3       1100000      1100000               11/10/2021  
4        644588        76706               11/10/2021  

[5 rows x 26 columns]

In [60]:
df.rename(columns={'NÚMERO PEDIDO': 'Numero_Pedido',
                  'ORDEN NÚMERO': 'Orden_Numero',
                  'FECHA ORDEN': 'Fecha_Orden',
                  'FECHA ENTREGA': 'Fecha_Entrega',
                  'FECHA APROBACION': 'Fecha_Aprobacion',
                  'CATEGORÍA': 'Categoria',
                  'SUBCATEGORIA': 'Subcategoria',
                  'PROVEEDOR': 'Proveedor',
                  'USUARIO': 'Usuario',
                  'USUARIO APROBADOR': 'Usuario_Aprobador',
                  'DIRECCION PEDIDO': 'Direccion_Pedido',
                  'DIRECCION FACTURACION': 'Direccion_Facturacion',
                  'CENTRO DE COSTOS': 'Centro_Costos',
                  'PRESUPUESTO': 'Presupuesto',
                  'PORTAL': 'Portal',
                  'ESTADO': 'Estado',
                  'PRODUCTO O SERVICIO': 'Producto_Servicio',
                  'CODIGO PORTAL': 'Codigo_Producto',
                  'CANTIDAD PEDIDA': 'Cantidad_Pedida',
                  'CANTIDAD RECIBIDA': 'Cantidad_Recibida',
                  'PRECIO UNITARIO': 'Precio_Unitario',
                  'PRECIO UNITARIO + IVA': 'Precio_Unitario_IVA',
                  'IVA': 'IVA',
                  'TOTAL SIN IVA': 'Total_Sin_IVA',
                  'TOTAL + IVA': 'Total_IVA',
                  'FECHA ULTIMO MOVIMIENTO': 'Fecha_Ultimo_Movimiento'}, inplace=True)

In [61]:
df['Fecha_Orden'] = pd.to_datetime(df['Fecha_Orden'], format = "%m/%d/%Y")
df['Fecha_Entrega'] = pd.to_datetime(df['Fecha_Entrega'], format = "%m/%d/%Y")
df['Fecha_Aprobacion'] = pd.to_datetime(df['Fecha_Aprobacion'], format = "%m/%d/%Y")

In [62]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 23083 entries, 0 to 23082
Data columns (total 26 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   Numero_Pedido            23083 non-null  object        
 1   Orden_Numero             23083 non-null  object        
 2   Fecha_Orden              23083 non-null  datetime64[ns]
 3   Fecha_Entrega            18770 non-null  datetime64[ns]
 4   Fecha_Aprobacion         21950 non-null  datetime64[ns]
 5   Categoria                23083 non-null  object        
 6   Subcategoria             23083 non-null  object        
 7   Proveedor                23083 non-null  object        
 8   Usuario                  23083 non-null  object        
 9   Usuario_Aprobador        21950 non-null  object        
 10  Direccion_Pedido         23083 non-null  object        
 11  Direccion_Facturacion    10828 non-null  object        
 12  Centro_Costos            16672 n

In [131]:
df.describe().T

count           mean           std   min    25%  \
Cantidad_Pedida      23083.0     191.208232  1.946639e+03  0.27    2.0   
Cantidad_Recibida    16013.0      69.835325  1.040933e+03  0.00    2.0   
Precio_Unitario      23083.0   59149.630767  6.331279e+05  0.00  244.0   
Precio_Unitario_IVA  23083.0   63580.384395  7.239502e+05  0.00  103.0   
IVA                  23083.0    9264.859420  1.011564e+05  0.00   95.0   
Total_Sin_IVA        23083.0  430121.193216  3.123982e+06  0.00  816.0   
Total_IVA            23083.0  477529.760040  3.545482e+06  0.00  515.0   

                         50%       75%          max  
Cantidad_Pedida          7.0      40.0     120000.0  
Cantidad_Recibida        5.0      18.0      53620.0  
Precio_Unitario       1706.0   22274.0   33242814.0  
Precio_Unitario_IVA    833.0    9877.0   39558949.0  
IVA                    781.0    5067.0    6316135.0  
Total_Sin_IVA        32269.0  187669.5  299185326.0  
Total_IVA            11995.0  146054.5  356030538.0

In [97]:
profile = ProfileReport(df, title="Pandas Profiling Report", explorative=True)

In [98]:
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [63]:
df.drop(["Cantidad_Recibida", "Total_Sin_IVA", "IVA", "Codigo_Producto", "Direccion_Facturacion", "Centro_Costos", "Numero_Pedido", "Orden_Numero"], axis=1, inplace = True)

#### Data Cleaning

In [64]:
d3_Cantidad_Pedida = df['Cantidad_Pedida'].mean() + 3*df['Cantidad_Pedida'].std()
d3_Precio_Unitario = df['Precio_Unitario'].mean() + 3*df['Precio_Unitario'].std()
d3_Precio_Unitario_IVA = df['Precio_Unitario_IVA'].mean() + 3*df['Precio_Unitario_IVA'].std()
d3_Total_IVA = df['Total_IVA'].mean() + 3*df['Total_IVA'].std()

In [65]:
df = df[(df['Cantidad_Pedida'] < d3_Cantidad_Pedida) & (df['Precio_Unitario'] < d3_Precio_Unitario) & (df['Precio_Unitario_IVA'] < d3_Precio_Unitario_IVA) & (df['Total_IVA'] < d3_Total_IVA)]

In [105]:
profile2 = ProfileReport(df, title="Pandas Profiling Report", explorative=True)
profile2

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [108]:
df.groupby(["Estado"]).Cantidad_Pedida.describe()

count        mean         std   min    25%   50%  \
Estado                                                                      
Cancelado               1129.0   54.227192  293.055958  1.00   2.00   4.0   
Enviado                   10.0  213.800000  628.347533  1.00   1.25   6.0   
Finalizado Incompleto    934.0   28.777302  139.907961  1.00   1.00   3.0   
Orden Confirmada          10.0   11.300000   11.035800  1.00   3.25   7.0   
Orden Rechazada         1003.0   18.504686   77.727792  0.30   2.00   4.0   
Orden en Proceso        4716.0  158.705831  451.164165  0.50  12.00  60.0   
Pendiente por Aprobar     49.0   22.061224   38.821390  1.00   1.00   2.0   
Recibido               14719.0   42.742797  243.915238  0.27   2.00   5.0   
Recibido Parcial         158.0   59.930380  288.872509  1.00   3.00   7.0   

                          75%     max  
Estado                                 
Cancelado               12.00  5000.0  
Enviado                 11.00  2000.0  
Finalizado Incompleto    9.75  2400.0  
Orden Confirmada        17.25    36.0  
Orden Rechazada         12.00  2000.0  
Orden en Proceso       144.00  6000.0  
Pendiente por Aprobar   30.00   192.0  
Recibido                20.00  6000.0  
Recibido Parcial        16.00  2500.0

In [109]:
df.groupby(["Estado"]).Precio_Unitario.describe()

count           mean            std    min     25%  \
Estado                                                                        
Cancelado               1129.0   22688.993800  123160.490119    0.0  114.00   
Enviado                   10.0    4664.200000   10185.551682    0.0    9.00   
Finalizado Incompleto    934.0   11539.127409   46200.772831    2.0   80.50   
Orden Confirmada          10.0  156390.100000  465180.901833  188.0  650.25   
Orden Rechazada         1003.0   13191.742772   55040.467204    0.0  179.00   
Orden en Proceso        4716.0    6686.142070   62016.258198    0.0  369.00   
Pendiente por Aprobar     49.0   26584.000000  153002.315061    1.0   15.00   
Recibido               14719.0   34244.330797  125388.582807    0.0  274.00   
Recibido Parcial         158.0    2384.063291   15663.054323    1.0  244.00   

                          50%       75%        max  
Estado                                              
Cancelado               585.0  12521.00  1946964.0  
Enviado                  21.5    155.25    29412.0  
Finalizado Incompleto  1141.0  11092.00  1020000.0  
Orden Confirmada       9245.5  16916.00  1480000.0  
Orden Rechazada         623.0   7163.00  1000000.0  
Orden en Proceso        654.0   1181.00  1869400.0  
Pendiente por Aprobar   179.0    611.00  1067811.0  
Recibido               7163.0  31092.00  1891951.0  
Recibido Parcial        369.0    379.00   189587.0

#### Feature Engineering

In [ ]:
-Dias_Trasncurridos_Entrega: Fecha Entrega vs Fecha Orden
-Convertir estado: Rechazado a 1 y el resto a 0

In [66]:
df["Dias_Trasncurridos_Entrega"] = (df["Fecha_Entrega"] - df["Fecha_Orden"]).dt.days

In [69]:
df

Fecha_Orden Fecha_Entrega Fecha_Aprobacion                  Categoria  \
0      2021-11-10    2021-11-10       2021-11-10  Eléctricos y Electrónicos   
1      2021-11-10    2021-11-11       2021-11-10      Mercadeo y publicidad   
2      2021-11-10    2021-11-10       2021-11-10        Alimentos y Bebidas   
3      2021-11-10    2021-11-12       2021-11-10        Alimentos y Bebidas   
4      2021-11-10    2021-11-09       2021-11-10      Imprenta y litografía   
...           ...           ...              ...                        ...   
23078  2018-04-30           NaT       2018-05-01  Aseo, Cafetería y Oficina   
23079  2018-04-30           NaT       2018-05-01  Aseo, Cafetería y Oficina   
23080  2018-04-30           NaT       2018-05-01          Moda y accesorios   
23081  2018-04-30           NaT       2018-04-30          Moda y accesorios   
23082  2018-04-30           NaT       2018-04-30  Aseo, Cafetería y Oficina   

                                           Subcategoria      Proveedor  \
0      Lámparas y bombillas y componentes para lámparas    Proveedor 1   
1                                            Publicidad    Proveedor 2   
2                    Alimentos preparados y conservados    Proveedor 3   
3                   Productos de carne y aves de corral    Proveedor 4   
4                                                  Otra    Proveedor 5   
...                                                 ...            ...   
23078                            Elementos de papelería  Proveedor 229   
23079                            Elementos de papelería  Proveedor 229   
23080                                           Calzado  Proveedor 229   
23081                                           Calzado  Proveedor 229   
23082                            Elementos de papelería  Proveedor 229   

                       Usuario     Usuario_Aprobador Direccion_Pedido  \
0        Usuario solicitante 1   Usuario Aprobador 1      Direccion 1   
1        Usuario solicitante 2   Usuario Aprobador 2      Direccion 1   
2        Usuario solicitante 3   Usuario Aprobador 3      Direccion 2   
3        Usuario solicitante 4   Usuario Aprobador 4      Direccion 3   
4        Usuario solicitante 5   Usuario Aprobador 5      Direccion 4   
...                        ...                   ...              ...   
23078  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23079  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23080  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23081  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23082  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   

           Presupuesto              Portal            Estado  \
0        Presupuesto 1  Portal comprador 1  Orden en Proceso   
1        Presupuesto 2  Portal comprador 1          Recibido   
2        Presupuesto 3  Portal comprador 1  Orden en Proceso   
3        Presupuesto 4  Portal comprador 2  Orden en Proceso   
4                  NaN  Portal comprador 3          Recibido   
...                ...                 ...               ...   
23078  Presupuesto 918  Portal comprador 8          Recibido   
23079  Presupuesto 918  Portal comprador 8          Recibido   
23080  Presupuesto 918  Portal comprador 8          Recibido   
23081  Presupuesto 918  Portal comprador 8          Recibido   
23082  Presupuesto 918  Portal comprador 8          Recibido   

                                  Producto_Servicio  Cantidad_Pedida  \
0      PANEL LED SOBREPONER 24W REDONDO LUZ BLANCA               2.0   
1                           ACTIVIDADES COMERCIALES              1.0   
2                                           Lasagna             10.0   
3                     Pecho de Res Limpio/Sin Grasa             50.0   
4                     LIBRO CABEZA, CORAZON Y MANOS              7.0   
...                                             ...              ...   
23078             

In [68]:
## - Convertir estado: Rechazado a 1 y el resto a 0
df['Estado_label'] = df['Estado']


In [70]:
df.loc[df['Estado'] == 'Cancelado', 'Estado_label'] = 1
df.loc[df['Estado'] == 'Orden en Proceso', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Enviado', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Finalizado Incompleto', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Orden Confirmada', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Orden Rechazada', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Pendiente por Aprobar', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Recibido', 'Estado_label'] = 0
df.loc[df['Estado'] == 'Recibido Parcial', 'Estado_label'] = 0

In [73]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 22728 entries, 0 to 23082
Data columns (total 20 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   Fecha_Orden                 22728 non-null  datetime64[ns]
 1   Fecha_Entrega               18554 non-null  datetime64[ns]
 2   Fecha_Aprobacion            21606 non-null  datetime64[ns]
 3   Categoria                   22728 non-null  object        
 4   Subcategoria                22728 non-null  object        
 5   Proveedor                   22728 non-null  object        
 6   Usuario                     22728 non-null  object        
 7   Usuario_Aprobador           21606 non-null  object        
 8   Direccion_Pedido            22728 non-null  object        
 9   Presupuesto                 18258 non-null  object        
 10  Portal                      22728 non-null  object        
 11  Estado                      22728 non-null  object    

In [71]:
df['Estado_label']= df['Estado_label'].astype(str).astype(int)

In [72]:
df

Fecha_Orden Fecha_Entrega Fecha_Aprobacion                  Categoria  \
0      2021-11-10    2021-11-10       2021-11-10  Eléctricos y Electrónicos   
1      2021-11-10    2021-11-11       2021-11-10      Mercadeo y publicidad   
2      2021-11-10    2021-11-10       2021-11-10        Alimentos y Bebidas   
3      2021-11-10    2021-11-12       2021-11-10        Alimentos y Bebidas   
4      2021-11-10    2021-11-09       2021-11-10      Imprenta y litografía   
...           ...           ...              ...                        ...   
23078  2018-04-30           NaT       2018-05-01  Aseo, Cafetería y Oficina   
23079  2018-04-30           NaT       2018-05-01  Aseo, Cafetería y Oficina   
23080  2018-04-30           NaT       2018-05-01          Moda y accesorios   
23081  2018-04-30           NaT       2018-04-30          Moda y accesorios   
23082  2018-04-30           NaT       2018-04-30  Aseo, Cafetería y Oficina   

                                           Subcategoria      Proveedor  \
0      Lámparas y bombillas y componentes para lámparas    Proveedor 1   
1                                            Publicidad    Proveedor 2   
2                    Alimentos preparados y conservados    Proveedor 3   
3                   Productos de carne y aves de corral    Proveedor 4   
4                                                  Otra    Proveedor 5   
...                                                 ...            ...   
23078                            Elementos de papelería  Proveedor 229   
23079                            Elementos de papelería  Proveedor 229   
23080                                           Calzado  Proveedor 229   
23081                                           Calzado  Proveedor 229   
23082                            Elementos de papelería  Proveedor 229   

                       Usuario     Usuario_Aprobador Direccion_Pedido  \
0        Usuario solicitante 1   Usuario Aprobador 1      Direccion 1   
1        Usuario solicitante 2   Usuario Aprobador 2      Direccion 1   
2        Usuario solicitante 3   Usuario Aprobador 3      Direccion 2   
3        Usuario solicitante 4   Usuario Aprobador 4      Direccion 3   
4        Usuario solicitante 5   Usuario Aprobador 5      Direccion 4   
...                        ...                   ...              ...   
23078  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23079  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23080  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23081  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   
23082  Usuario solicitante 131  Usuario Aprobador 70     Direccion 81   

           Presupuesto              Portal            Estado  \
0        Presupuesto 1  Portal comprador 1  Orden en Proceso   
1        Presupuesto 2  Portal comprador 1          Recibido   
2        Presupuesto 3  Portal comprador 1  Orden en Proceso   
3        Presupuesto 4  Portal comprador 2  Orden en Proceso   
4                  NaN  Portal comprador 3          Recibido   
...                ...                 ...               ...   
23078  Presupuesto 918  Portal comprador 8          Recibido   
23079  Presupuesto 918  Portal comprador 8          Recibido   
23080  Presupuesto 918  Portal comprador 8          Recibido   
23081  Presupuesto 918  Portal comprador 8          Recibido   
23082  Presupuesto 918  Portal comprador 8          Recibido   

                                  Producto_Servicio  Cantidad_Pedida  \
0      PANEL LED SOBREPONER 24W REDONDO LUZ BLANCA               2.0   
1                           ACTIVIDADES COMERCIALES              1.0   
2                                           Lasagna             10.0   
3                     Pecho de Res Limpio/Sin Grasa             50.0   
4                     LIBRO CABEZA, CORAZON Y MANOS              7.0   
...                                             ...              ...   
23078             

In [9]:
def heatmap(df):
    df = df[['x', 'y', 'ppscore']].pivot(columns='x', index='y', values='ppscore')
    ax = sns.heatmap(df, vmin=0, vmax=1, cmap="Blues", linewidths=0.5, annot=True)
    ax.set_title("PPS matrix")
    ax.set_xlabel("feature")
    ax.set_ylabel("target")
    return ax

In [10]:
matrix =pps.matrix(df)

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: Us

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: Us

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: Us

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: Us

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: Us

C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)
C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_split.py:668: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=4.
  % (min_groups, self.n_splits)), UserWarning)


In [12]:
heatmap(matrix)

<AxesSubplot:title={'center':'PPS matrix'}, xlabel='feature', ylabel='target'>

In [13]:
def corr_heatmap(df):
    ax = sns.heatmap(df, vmin=-1, vmax=1, cmap="BrBG", linewidths=0.5, annot=True)
    ax.set_title("Correlation matrix")
    return ax

In [14]:
corr_heatmap(df.corr())

<AxesSubplot:title={'center':'Correlation matrix'}>

In [74]:
## cambio de variables categoricas con labelencode
lb_encoder = LabelEncoder()
df["Categoria_label_encode"] = lb_encoder.fit_transform(df["Categoria"])
df["Subcategoria_label_encode"] = lb_encoder.fit_transform(df["Subcategoria"])
df["Proveedor_label_encode"] = lb_encoder.fit_transform(df["Proveedor"])
df["Usuario_label_encode"] = lb_encoder.fit_transform(df["Usuario"])
df["Usuario_Aprobador_label_encode"] = lb_encoder.fit_transform(df["Usuario_Aprobador"])
df["Direccion_Pedido_label_encode"] = lb_encoder.fit_transform(df["Direccion_Pedido"])
df["Presupuesto_label_encode"] = lb_encoder.fit_transform(df["Presupuesto"])
df["Portal_label_encode"] = lb_encoder.fit_transform(df["Portal"])
df["Producto_Servicio_encode"] = lb_encoder.fit_transform(df["Producto_Servicio"])

In [76]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 22728 entries, 0 to 23082
Data columns (total 29 columns):
 #   Column                          Non-Null Count  Dtype         
---  ------                          --------------  -----         
 0   Fecha_Orden                     22728 non-null  datetime64[ns]
 1   Fecha_Entrega                   18554 non-null  datetime64[ns]
 2   Fecha_Aprobacion                21606 non-null  datetime64[ns]
 3   Categoria                       22728 non-null  object        
 4   Subcategoria                    22728 non-null  object        
 5   Proveedor                       22728 non-null  object        
 6   Usuario                         22728 non-null  object        
 7   Usuario_Aprobador               21606 non-null  object        
 8   Direccion_Pedido                22728 non-null  object        
 9   Presupuesto                     18258 non-null  object        
 10  Portal                          22728 non-null  object        
 11  Es

In [77]:
#ligth gb      
    
# Split training data in to training and validation sets.
# Validation set is used for early stopping.
    
X = df.drop(['Fecha_Orden','Fecha_Entrega','Fecha_Aprobacion','Categoria','Subcategoria','Proveedor','Usuario','Usuario_Aprobador','Direccion_Pedido','Presupuesto','Portal','Estado','Producto_Servicio','Fecha_Ultimo_Movimiento','Estado_label'], axis=1)
y = df['Estado_label']
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.4, random_state=1234)
train_data = lgb.Dataset(X_train, label=y_train)
valid_data = lgb.Dataset(X_valid, label=y_valid, reference=train_data)

In [78]:
X

Cantidad_Pedida  Precio_Unitario  Precio_Unitario_IVA  Total_IVA  \
0                  2.0            23364                27803      55606   
1                  1.0          1476972              1757597    1757597   
2                 10.0              155                  155        155   
3                 50.0               22                   22    1100000   
4                  7.0            92084                10958      76706   
...                ...              ...                  ...        ...   
23078              8.0            33613                   40        320   
23079              1.0              588                  700        700   
23080              3.0            29412                   35        105   
23081              4.0            29412                   35        140   
23082              5.0            33613                   40        200   

       Dias_Trasncurridos_Entrega  Categoria_label_encode  \
0                             0.0                      10   
1                             1.0                      21   
2                             0.0                       1   
3                             2.0                       1   
4                            -1.0                      16   
...                           ...                     ...   
23078                         NaN                       3   
23079                         NaN                       3   
23080                         NaN                      24   
23081                         NaN                      24   
23082                         NaN                       3   

       Subcategoria_label_encode  Proveedor_label_encode  \
0                             70                       0   
1                            106                     105   
2                              6                     207   
3                            100                     314   
4                             88                     330   
...                          ...                     ...   
23078                         39                     132   
23079                         39                     132   
23080                         18                     132   
23081                         18                     132   
23082                         39                     132   

       Usuario_label_encode  Usuario_Aprobador_label_encode  \
0                         0                               0   
1                        46                              11   
2                        57                              22   
3                        68                              33   
4                        79                              43   
...                     ...                             ...   
23078                    34                              65   
23079                    34                              65   
23080                    34                              65   
23081                    34                              65   
23082                    34                              65   

       Direccion_Pedido_label_encode  Presupuesto_label_encode  \
0                                  0                         0   
1                                  0                       101   
2                                 87                       207   
3                                 98                       305   
4                                109                       875   
...                              ...                       ...   
23078                            154                       863   
23079                            154                       863   
23080                            154                       863   
23081                            154                       863   
23082                            154                       863   

       Portal_label_encode  Producto_Servicio_encode  
0                        0                     

In [97]:
y_valid.value_counts() 

0    8622
1     470
Name: Estado_label, dtype: int64

In [103]:
X_valid

Cantidad_Pedida  Precio_Unitario  Precio_Unitario_IVA  Total_IVA  \
9737               5.0             3282                 3282       1641   
909                1.0             2311                27501      27501   
8557               2.0            83294                83294     166588   
8687               5.0             6944                 6944      34719   
6461               1.0               95                11305      11305   
...                ...              ...                  ...        ...   
7303               0.5                8                    8          4   
17534              2.0            86555                  103        206   
465                4.0            31595                31595      12638   
5935               1.0              600                  714        714   
13621              5.0            86555                  103        515   

       Dias_Trasncurridos_Entrega  Categoria_label_encode  \
9737                          1.0                       1   
909                           4.0                      11   
8557                          2.0                       1   
8687                          1.0                       1   
6461                          3.0                      11   
...                           ...                     ...   
7303                          1.0                       1   
17534                         0.0                      35   
465                          10.0                       3   
5935                          0.0                      21   
13621                         0.0                      35   

       Subcategoria_label_encode  Proveedor_label_encode  \
9737                          29                     144   
909                           58                     228   
8557                         105                     303   
8687                           6                     163   
6461                          58                      65   
...                          ...                     ...   
7303                         142                     163   
17534                        115                     210   
465                           36                     340   
5935                         106                     343   
13621                        115                     210   

       Usuario_label_encode  Usuario_Aprobador_label_encode  \
9737                     68                              33   
909                       1                              54   
8557                     68                              33   
8687                     98                              70   
6461                     86                              69   
...                     ...                             ...   
7303                     98                              33   
17534                    25                              55   
465                       0                               0   
5935                     56                               5   
13621                    25                              55   

       Direccion_Pedido_label_encode  Presupuesto_label_encode  \
9737                              98                       875   
909                               87                       550   
8557                              98                       875   
8687                             115                       875   
6461                             120                       341   
...                              ...                       ...   
7303                              98                       875   
17534                             44                       648   
465                                0                       325   
5935                             120                       249   
13621                             15                       821   

       Portal_label_encode  Producto_Servicio_encode  
9737                    10                     

In [79]:
## sin grid search 
SEARCH_PARAMS = {'learning_rate': 0.4,
                'max_depth': 15,
                'num_leaves': 32,
                'feature_fraction': 0.8,
                'subsample': 0.2}

FIXED_PARAMS={'objective': 'binary',
             'metric': 'auc',
             'is_unbalance':True,
             'bagging_freq':5,
             'boosting':'dart',
             'num_boost_round':300,
             'early_stopping_rounds':30}



In [81]:
params = {'metric':FIXED_PARAMS['metric'],
             'objective':FIXED_PARAMS['objective'],**SEARCH_PARAMS}

In [82]:
model = lgb.train(params, train_data,                     
                     valid_sets=[valid_data],
                     num_boost_round=FIXED_PARAMS['num_boost_round'],
                     early_stopping_rounds=FIXED_PARAMS['early_stopping_rounds'],
                     valid_names=['valid'])

[LightGBM] [Info] Number of positive: 659, number of negative: 12977
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000557 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2098
[LightGBM] [Info] Number of data points in the train set: 13636, number of used features: 14
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.048328 -> initscore=-2.980210
[LightGBM] [Info] Start training from score -2.980210
[1]	valid's auc: 0.895567
Training until validation scores don't improve for 30 rounds
[2]	valid's auc: 0.905462
[3]	valid's auc: 0.910245
[4]	valid's auc: 0.915469
[5]	valid's auc: 0.921741
[6]	valid's auc: 0.92358
[7]	valid's auc: 0.924094
[8]	valid's auc: 0.925903
[9]	valid's auc: 0.926165
[10]	valid's auc: 0.929977
[11]	valid's auc: 0.930327
[12]	valid's auc: 0.933526
[13]	valid's auc: 0.932086
[14]	valid's auc: 0.932267
[15]	valid's

C:\Users\d84088661\Anaconda3\lib\site-packages\lightgbm\engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "


In [100]:
score = model.best_score['valid']['auc']

In [101]:
score

0.9387054146493138

In [123]:
## score de test
y_predict = model.predict(X_valid)


In [130]:
y_predict

array([1.00008631e-02, 5.78647260e-03, 2.54723168e-03, ...,
       2.22722805e-04, 2.60170303e-03, 8.37942316e-06])

In [125]:
y_predict2 = model.predict(X_valid, num_iteration=model.best_iteration)

In [110]:
num_iteration =model.best_iteration
num_iteration

36

In [127]:
#convert into binary values	
for i in range(0,35):	
    if y_predict2[i]>=.5:       # setting threshold to .5	
            y_predict2[i]=1
    else:
        y_predict2[i]=0

In [128]:
y_predict2

array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
       2.22722805e-04, 2.60170303e-03, 8.37942316e-06])

In [132]:
accuracy=accuracy_score(y_valid,y_predict)

ValueError: Classification metrics can't handle a mix of binary and continuous targets

In [114]:
y_predict

array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
       2.22722805e-04, 2.60170303e-03, 8.37942316e-06])

In [98]:
print(classification_report(y_valid, y_predict))

ValueError: Classification metrics can't handle a mix of binary and continuous targets

In [42]:
# Set params
# Scores ~0.784 (without tuning and early stopping)
params = {'boosting_type': 'gbdt', 'max_depth': -1, 'objective': 'binary', 
          'num_leaves': 64, 'learning_rate': 0.05, 'max_bin': 512, 
          'subsample_for_bin': 200, 'subsample': 1, 'subsample_freq': 1,
          'colsample_bytree': 0.8, 'reg_alpha': 5, 'reg_lambda': 10, 
          'min_split_gain': 0.5, 'min_child_weight': 1, 
          'min_child_samples': 5, 'scale_pos_weight': 1, 'num_class': 1, 
          'metric': 'binary_error'}

# Create parameters to search
grid_params = {'learning_rate': [0.01], 'n_estimators': [8, 24],
               'num_leaves': [6, 8, 12, 16], 'boosting_type': ['gbdt'], 
               'objective': ['binary'], 'seed': [500],
               'colsample_bytree': [0.65, 0.75, 0.8], 
               'subsample': [0.7, 0.75], 'reg_alpha': [1, 2, 6],
               'reg_lambda': [1, 2, 6]}

In [43]:
# Create classifier to use. Note that parameters have to be input manually
# not as a dict!
mod = lgb.LGBMClassifier(**params)
    
# To view the default model params:
mod.get_params().keys()

dict_keys(['boosting_type', 'class_weight', 'colsample_bytree', 'importance_type', 'learning_rate', 'max_depth', 'min_child_samples', 'min_child_weight', 'min_split_gain', 'n_estimators', 'n_jobs', 'num_leaves', 'objective', 'random_state', 'reg_alpha', 'reg_lambda', 'silent', 'subsample', 'subsample_for_bin', 'subsample_freq', 'max_bin', 'scale_pos_weight', 'num_class', 'metric'])

In [44]:
# Create the grid
grid = GridSearchCV(mod, param_grid=grid_params, verbose=1, cv=5, n_jobs=-1)
# Run the grid
grid.fit(X_train, y_train)

Fitting 5 folds for each of 432 candidates, totalling 2160 fits


C:\Users\d84088661\Anaconda3\lib\site-packages\sklearn\model_selection\_search.py:925: UserWarning: One or more of the test scores are non-finite: [nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan nan
 nan nan nan nan nan nan nan nan nan nan nan nan n

ValueError: DataFrame.dtypes for data must be int, float or bool.
Did not expect the data types in the following fields: Fecha_Orden, Fecha_Entrega, Fecha_Aprobacion, Categoria, Subcategoria, Proveedor, Usuario, Usuario_Aprobador, Direccion_Pedido, Presupuesto, Portal, Estado, Producto_Servicio, Fecha_Ultimo_Movimiento

In [ ]:
 # Print the best parameters found
    print(grid.best_params_)
    print(grid.best_score_)

In [ ]:
    # Using parameters already set above, replace in the best from the grid search
    best_params = {k: grid.best_params_.get(k, v) for k, v in params.items()}
    best_params['verbosity'] = -1

    # Kit k models with early-stopping on different training/validation splits
    k = 5
    valid_preds, train_preds, test_preds = 0, 0, 0
    for m in range(k):
        print('Fitting model', m)

        # Prepare the data set for fold
        X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.4, random_state=1234)
        
         # Train
        gbm = lgb.train(best_params, train_data, num_boost_round=100000,
                        valid_sets=[train_data, valid_data],
                        early_stopping_rounds=50, verbose_eval=50)

        # Plot importance
        lgb.plot_importance(gbm)
        plt.show()
